In [1]:
import tarfile,sys
import pandas as pd
import os
import re as regex
import numpy as np
import torch
import torch.nn as nn
from torch.autograd import Variable
from torch import optim
import torch.nn.functional as F
import torch.nn as nn
from torch.autograd import Variable
import torch.nn.functional as F
from sklearn.preprocessing import LabelEncoder
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import GaussianNB
from sklearn.model_selection import cross_val_score
from sklearn.linear_model import LogisticRegression
import seaborn as sns
import numpy
import matplotlib.pyplot as plt
from sklearn.metrics import confusion_matrix
import chakin

## Read from CSV file containing features

In [2]:
#testdata = pd.read_csv('test.csv')
traindata = pd.read_csv('train-small')
traindata.head()

Unnamed: 0       class    user_name                   id  \
0           0  depression  k1Tgty92JWM  6195046850825297023   
1           0     control     f8Da_Rvi  8522289883066978092   
2           0  depression  hehQgSVVRpv   322688550056773303   
3           0     control  qPQRyK39gnG  2184602040112857282   
4           0  depression  j_1H5RgR2_6  2834216959061162834   

                                               tweet  avgsentiment  \
0  RT @FpJgkXU6: My cat is sad because, having be...      0.112638   
1  Running Boston for Children's Hospital again. ...      0.118159   
2  My mom is just swell like that. :)####In other...      0.047492   
3  Ain't nothing like starting your morning with ...      0.099925   
4  RT @GAndbcDpitkbVU: #ThePinkPrintCoverTomorrow...      0.211423   

   favorite_count  firstperson  geo  possibly_sensitive  retweet_count  \
0               0         2670  NaN                 0.0            249   
1               0          142  NaN                 0.0              1   
2               0         2562  NaN                 NaN              0   
3               0         2592  NaN                 NaN              0   
4               0         2891  NaN                 NaN             10   

   retweeted  tsugawa  number_of_uppercase  number_of_exclamation  \
0      False        0                    2                      0   
1      False        0                    0                      0   
2      False        0                    1                      0   
3      False        0                    1                      1   
4      False        0                    2                      0   

   number_of_question  number_of_ellipsis  
0                   0                   0  
1                   0                   0  
2                   0                   0  
3                   0                   0  
4                   0                   0

In [3]:
# b = pd.DataFrame(traindata['tweet'].str.split('####').tolist(), index=[traindata['user_name'], traindata['class'], traindata['avgsentiment'], traindata['favorite_count'], traindata['firstperson'], traindata['geo'], traindata['possibly_sensitive'], traindata['retweet_count'], traindata['retweeted'], traindata['tsugawa'], traindata['number_of_uppercase'], traindata['number_of_exclamation'], traindata['number_of_question'], traindata['number_of_ellipsis']]).stack()
# b = b.reset_index()[[0, 'user_name','class', 'avgsentiment', 'favorite_count', 'firstperson', 'geo', 'possibly_sensitive', 'retweet_count', 'retweeted', 'tsugawa', 'number_of_uppercase', 'number_of_exclamation', 'number_of_question', 'number_of_ellipsis']] 
# b.columns = ['tweet', 'user_name','class', 'avgsentiment', 'favorite_count', 'firstperson', 'geo', 'possibly_sensitive', 'retweet_count', 'retweeted', 'tsugawa', 'number_of_uppercase', 'number_of_exclamation', 'number_of_question', 'number_of_ellipsis'] 
# final_train_data = b
b = pd.DataFrame(traindata['tweet'].str.split('####').tolist(), index=[traindata['user_name'], traindata['class']]).stack()
b = b.reset_index()[[0, 'user_name','class']] # var1 variable is currently labeled 0
b.columns = ['tweet', 'user_name','class'] # renaming var1
final_train_data = b

In [4]:
final_train_data.head()

tweet    user_name       class
0  RT @FpJgkXU6: My cat is sad because, having be...  k1Tgty92JWM  depression
1  @r2kbk0ooSf7 @gJX64gO487acDT hope it works out...  k1Tgty92JWM  depression
2  @r2kbk0ooSf7 Good thanks. Really good. Enjoyin...  k1Tgty92JWM  depression
3  Kids have a new game. Let's try to strangle ea...  k1Tgty92JWM  depression
4  4yo thinks she has one foot bigger than the ot...  k1Tgty92JWM  depression

## Clean Up data

In [5]:
def remove_by_regex(tweets, regexp):
    tweets.loc[:, "tweet"].replace(regexp, "", inplace=True)
    return tweets

def remove_urls(tweets):
    return remove_by_regex(tweets, regex.compile(r"http.?://[^\s]+[\s]?"))

def remove_na(tweets):
    return tweets[tweets["tweet"] != "Not Available"] 

def remove_empty(tweets):
    return tweets[tweets["tweet"] != " "]

def remove_special_chars(tweets):  # it unrolls the hashtags to normal words
    for remove in map(lambda r: regex.compile(regex.escape(r)), [",", ":", "\"", "=", "&", ";", "%", "$",
                                                                 "@", "%", "^", "*", "(", ")", "{", "}",
                                                                 "[", "]", "|", "/", "\\", ">", "<", "-",
                                                                 "!", "?", ".", "'",
                                                                 "--", "---", "#"]):
        tweets.loc[:, "tweet"].replace(remove, "", inplace=True)
    return tweets

def remove_usernames(tweets):
    return remove_by_regex(tweets, regex.compile(r"@[^\s]+[\s]?"))

def remove_numbers(tweets):
    return remove_by_regex(tweets, regex.compile(r"\s?[0-9]+\.?[0-9]*"))

In [6]:
data = final_train_data
data = remove_urls(data)
data = remove_na(data)
data= remove_empty(data)
data = remove_usernames(data)
data = remove_special_chars(data)
data = remove_numbers(data)
#data.cleanup(TwitterCleanuper())

In [7]:
#data=data.head(20000)

In [8]:
def tokenize(tweet):
        # Tokenize file content
    ids = torch.ByteTensor(len(tweet.encode()))
    token = 0
    for char in tweet.encode():
        ids[token] = char
        token += 1

    return ids

def batchify(data, bsz):
    nbatch = data.size(0) // bsz
    data = data.narrow(0, 0, nbatch * bsz)
    data = data.view(bsz, -1).t().contiguous()
    return data   

In [9]:
x = data.query('tweet != ""')
x.shape
data=x
data = data[data.tweet.str.split(' ').str.len() > 1]
data=data.reset_index(drop=True)

In [10]:
data.shape

(86415, 3)

In [11]:
def copy_state(state):
    if isinstance(state, tuple):
    	return (Variable(state[0].data), Variable(state[1].data))
    else:
    	return Variable(state.data) 

def batchify(data, bsz):
    nbatch = data.size(0) // bsz
    data = data.narrow(0, 0, nbatch * bsz)
    data = data.view(bsz, -1).t().contiguous()
    return data        


In [12]:
def update_lr(optimizer, lr):
    for group in optimizer.param_groups:
        group['lr'] = lr
    return
	
def clip_gradient_coeff(model, clip):
    """Computes a gradient clipping coefficient based on gradient norm."""
    totalnorm = 0
    for p in model.parameters():
        modulenorm = p.grad.data.norm()
        totalnorm += modulenorm ** 2
    totalnorm = math.sqrt(totalnorm)
    return min(1, clip / (totalnorm + 1e-6))

def calc_grad_norm(model):
    """Computes a gradient clipping coefficient based on gradient norm."""
    totalnorm = 0
    for p in model.parameters():
        modulenorm = p.grad.data.norm()
        totalnorm += modulenorm ** 2
    return math.sqrt(totalnorm)
    
def calc_grad_norms(model):
    """Computes a gradient clipping coefficient based on gradient norm."""
    norms = []
    for p in model.parameters():
        modulenorm = p.grad.data.norm()
        norms += [modulenorm]
    return norms
    
def clip_gradient(model, clip):
    """Clip the gradient."""
    totalnorm = 0
    for p in model.parameters():
        print(p)
        p.grad.data = p.grad.data.clamp(-clip,clip)

In [ ]:

class Net(nn.Module):
    def __init__(self, features, cls_size):
        super(Net, self).__init__()
        self.hidden_size = 256
        self.embedding = nn.Embedding(features, self.hidden_size)
        self.rnn1 = nn.GRU(input_size=features,
                            hidden_size=self.hidden_size)
        self.dense1 = nn.Linear(self.hidden_size, cls_size)

    def forward(self, x, hidden):
        output, hidden = self.rnn1(x, hidden)
        #output = self.dense1(output)
        return output, hidden

    def init_hidden(self, batch_size=1):
        weight = next(self.parameters()).data
        return Variable(weight.new(1, batch_size, self.hidden_size).zero_())

def var(x):
    x = Variable(x)
    return x

embed = nn.Embedding(256, 50)    
embed_optimizer = optim.SGD(embed.parameters(), lr=0.005)

model = Net(features=50, cls_size=256)
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-2)
hiddens=[]
rnn = model

def train():
    hiddenCounter=0
    model.train()
    batch_size = 1
    hidden_init = model.init_hidden(1)
    loss_avg = 0
    for s in range(data.shape[0]):
        model.zero_grad()
        embed_optimizer.zero_grad()
        hidden = hidden_init
        loss =0
        tweet=data.loc[s].tweet
        print (tweet)
        emb = tokenize(tweet)
        embLen=len(emb)
        if (embLen!=1) & (emb[0]!=32):
            for i in range(embLen): 
                character1=Variable((torch.Tensor([emb[i]])).long())
                character1=embed(character1)
                character1=character1.view(1,1,50)

                output, hidden = model(character1, var(hidden.data))
                output=output.view(1,256)

                if i+1 < embLen: 
                    character2=Variable((torch.Tensor([emb[i+1]])).long())
                    loss += criterion(output, character2)
            #print (loss)
            loss.backward()
            tempHidden=hidden.view(256)
            tempHidden=list(tempHidden.data.numpy())
            hiddens.append(tempHidden)
            hidden_init = copy_state(hidden)
            optimizer.step()
            embed_optimizer.step()
            loss_avg = .99*loss_avg + .01*loss.data[0]/embLen

        if s % 10000 == 0:
            print(epoch, s, loss_avg)

for epoch in range(1):
    print(model.parameters())
    hiddens=[]
    train()

<generator object Module.parameters at 0x7f3309af4308>
RT My cat is sad because having been targeted by Internet trolls he must now live with a hour bodyguard 
0 0 0.0549364236684946
hope it works out well Xx
Good thanks Really good Enjoying life on the other side How are you
Kids have a new game Lets try to strangle each other Brilliant This cant possibly go wrong
yo thinks she has one foot bigger than the other and is utterly fascinated by this fact Shes making a bid for new shoe
What are the odds of theyo remembering its hot today and drinking lots of water zilch I might save time by recording my voice
lol something happens once and people just dont forget
Im really good Things are going well How are you Xxx
Im sorry It gets complicated managing work Twitter accounts and Im always paranoid Ill tweet from the wrong one
RT You can only genuinely like yourself if you can acknowledge that you have or are a work in progress continually developi…
Those arent really my areas but Ill have a

If is as shit as New Years Eve is turning out to be I might not bother with it
We skyped the abroad relies too It does help Had a lovely time thanks Hope you have Xx
I have a hangover and theyo hasnt stopped shouting singing and talking since she got up Where is the quiet button
Nothing says social pariah quite like a veruca sock
Ahyos at schoolyos at preschool I have tea cake and netflix and Im not moving till I have to pick theyo up
Could it actually be bedtime and weve all got confused hopeful face
Is it really morning or is someone playing a sick joke Ive had next to no sleep and my phones playing up again grumps off
They really are sometimes
Oh that sounds good 
He wouldnt hear He sleeps too heavily sighs
Lets hope so X
Things have improved Till the next phase Poor little thing Teething is just rubbish
Seriously Cant they just be a bit careful He use to fall on the bed putting his socks on and wake me up shaking the bed
my kids have gone through various early morning phases Each o

Court on your day off is just mean
I like to live in hope
Im so tired Id give away chocolate for more sleep This may shock people
Mmmm contemplates a very big decision there I think it depends how quickly and sensibly they get dressed 
Morning peeps Cant think of many things I wouldnt give away now for another hours in bed
Lol I like your thinking
With the Just because or I just did reasoning Kids Whod have them if they knew
Nothing like starting the day with a large row with ayo Is it bedtime yet
Much sympathy Weeks like that are tough
Its really getting on my nerves How are you
Lol I know I few people whove had a cold its taken forever to throw off Hoping thats not happening to me
Im hoping to feel like that when my germs finally take a hike
Eugh Monday And I still have THE COLD Hows everyone else doing
RT My letter to Jeff Bezos and all about removing THAT BOOK from sale now includes the petitions Please RT 
http…
Oh yes I drink tea and coffee but not BeechamsLemsip drinks
I take th

I know Who doesnt have normal sugar but has the others What can I say I like baking
End of term v possibly Or is he drinking water in school Mine doesnt amp this is an ongoing problem Affects lots of things
Ive just had to put icing sugar in the plumbers tea as weve run out of normal It was either that or vanilla sugar or light muscovado
Ha ha Might have to invest in a canoe
YES Cant wait for a break  Off for a couple of days away tomorrow all together Will be lovely if wet
RT Vitamin D tablets for free Why bother when theres an app for that sun
Im going to try to remember the moment when theyre trying to kill each other
This morning I heardyo wake up and whisper I love you to her big bro on the other side of the room toocute
It surely can
Yes it is I hope we get to know each other well again
Sleep my old friend it was so lovely to see you again properly last night
Ill have a look Probably tomorrow Im so tired I dont think I could work a search tool now
Im afraid I havent seen it so th

It is a genius strategy But disappointing when youre winning
Half way through snakes and ladders and it looks like victory is minesoyo announces its boring and says lets play something else
Why do coat their raisins in oil Its unnecesary Plus palm oil is not a good choice Id like my raisins wo oil + deforestation
I forgot to wash my hair last night plasters it in dry shampoo
I know Its not right
Lol always nice to be missed  I have been a busy little bee But expect normal service to return shortly
I think it has to
Worse nights sleep in a long time Man Im grumpy
Thank you You too
Yep That sums it up 
RT saw this on the other social networking site and it reminded me of your tweet of yesterday 
Oh riiiiiiiight
I couldnt agree more
It is Most strange And theres a lot of fog Its quite spooky
I know Unbelievable
Have I woken up in
And smoking in the car with the windows up and two kids in the car
Whats with people on the school run not having their kids strapped in and not using car seats 

...

lol umm lil booty noooo we not But damn put us on blast sis
I told Oomfs I wasnt messing with him no more this man talking bout he going to make his way out here umm Im lost
So you coming this weekend frfr
RT Me n oomf are about to fight
RT You Can t Be A Female An You Out Here Fucking Any  Everything
thanks girl me too But you said some real shit
RT And i hope your son get well soon
Who you trying to tweet bruh
Hell yea frfr plus we need one for socialcam
Lmao I didnt kno fool
RT If you have to change for the satisfaction of another  then it wont work because they never accepted you for you
We need to get our classes started
RT Dont blame everything on the nigga in a relationship because sometimes you need to fault yourself because its act 
I put it in my bd hands thats his brother so maybe he need to find out his problem I dont have to deal with him
Lol yea its been a minute I think it hasnt been since Dave slept with ussum lmao
Oomfs said I made him feel lame teeheehee my bad made y

mama charra you wasnt suppose to see those last couple of tweets lol
whats all that poken from the back
RT come give me some
Im on the way freak
Im need some of that last Thursday action I need to hit his line like now
I need some good head before bed
RT twitterafterdark role play is a must
RT I love my mama though
I need some grown folks attention dont be surprise if your phone starts to ring yea you not you but you
I enjoyed my Sunday family time is always priceless now home I go
lol they miss you too
Does anybody miss juju
I think its time to get dress so I can go beat the fam ass in bowling
Ive been laying around all day in nothing but a tshirt
o ok
o ok so yall ate good
lol did you watch it again
RT Single for the moment lol
I cant wait to get you fucked up and a birthday dance
I guess make up sex is the best sex cause white girl forgot her man was cheating lmao
RT If i was depending on a bitch i wont have shit
RT All kids are a blessing and I truly thank god 🙏 for blessing me wit

Driving down the highway who wants to be the DJ
RT Mondays are so much better after a win GoBrowns
im not
shut your mouth
its too long
my hair Is sodamn long lol
RT “Not getting my haircut until we lose” Im doin that too and its gettin rough
to answer your question jordan she does not know he is up 
That move was nasty
RT Youll be just a memory in the back of my mind
There is just something about Kent State I like My brother being successful from there and lots of family FutureFlash 
Someone text me
Hmm what to do today
hahaha love you
Moeglin is special needs 
atta girl lol
RT He will always be my dude 👌☺️ 
This sucks
Not much to do tonight
You dont block Then you dont fall on it
you looked gay as normal
yes lol
good luck dude
Todays one of my favorite days of the year
Theres only two undefeated teams in Stark County football and they both have an Austin Shaheen 
RT Theres only two undefeated teams in Stark County football and they both have an Austin Shaheen words of 
Good luck today

Someone text me
RT Why is it so hard to find a TRUE relationship
yes lol
she told me I was not loved as a child 
always looking to make a difference in this world and this is a great opportunity to do so
Had a really good time tonight Love being with the right people
Todays officials have been selected by the OHSAA
Polumalu knows how to hit to bad his team does not know how to win
Haunted houses are the bomb
Well fantasy owners of AP be ready for a monster day
Not to sure whats going on tonight
Browns got it again today
im teasing love you
sorry I dont speaknd place
lol your sad
whats up runner up 
might be heading over to fawcett this evening
Too tired to fist myself today😂✋ well thats strange
I honesty called this one
Kills me
no problem always
haha both spellings sound the same it was a hard one
Why isnt my phone getting texts Is it the phone
 Or is it you Life questions Francis
RT its crazy how seeing one picture or one thing can change your mood in a split second
the love is much 

lol long season ahead
you Act like tom Brady and jimmy gram are easy to beat
I mean I believe youre but him Idk about that
youre right 😔
youre so gay
RT Sometimes you just have to risk it
the whole bench is violent
Tony is sending me one word text over Richardson leaving Browns
Browns new running back browns 
You have to be kidding me browns WTF
RT Browns shirt todaygtgtgt DontHate StayLoyal
happy birthday teammate
Dont care what anyone says ill always be proud the wear my browns stuff NoShame
RT Alright Perez no fucking around
Watched some old NCAA basketball film on YouTube of great games and you better bet was announcing them GreatestOfAllTime Legend
is back on Great time to waste my night watching my step sons show INailedYourMom  fag
RT dats cuz u da shit
thanks chick
Ask anyone from any school outside of Louisville I get along with them no matter what color their skin is and Im not the only one this way
“Ive walked back and forth from my dorm to the gay library twice because I ke

In [46]:
data[data['tweet'].str.contains("RT A wonderful")]

tweet       user_name  \
12239  RT A wonderful interview with the great Larry ...  vlwXqvDcXHd8vR   

         class  
12239  control

In [84]:
problems=data.iloc[12239:12248]

In [85]:
problems.reset_index(drop=True)

tweet       user_name    class
0  RT A wonderful interview with the great Larry ...  vlwXqvDcXHd8vR  control
1                                                     vlwXqvDcXHd8vR  control
2  RT One of the most admirable beautiful and hea...  vlwXqvDcXHd8vR  control
3  Should have had a drinking game with SNL and t...  vlwXqvDcXHd8vR  control
4  my feelings too Everyone should read The Tippi...  vlwXqvDcXHd8vR  control
5  RT For my own body I am prolife But I believe ...  vlwXqvDcXHd8vR  control
6  Everyday this week Crap I think that makes me ...  vlwXqvDcXHd8vR  control
7  RT My autobiographer just made another pass at...  vlwXqvDcXHd8vR  control
8  RT There hasnt been a scandal this big at the ...  vlwXqvDcXHd8vR  control

In [79]:
problems.iloc[0]

tweet        RT A wonderful interview with the great Larry ...
user_name                                       vlwXqvDcXHd8vR
class                                                  control
Name: 12239, dtype: object

In [50]:
data.loc[[12240]]

tweet       user_name    class
12240        vlwXqvDcXHd8vR  control

In [ ]:
hiddens=np.squeeze(hiddens)

In [ ]:
# hiddenDF=pd.DataFrame(hiddens)
# allFeatures = pd.concat([hiddenDF, extraFeatures], axis=1)
# allFeatures.head()

## Classifiers

In [ ]:
crisisEncoder = LabelEncoder()
y = crisisEncoder.fit_transform(data['class'])
print (crisisEncoder.classes_)
print(y)
print(data.tweet[0])

In [ ]:
log = cross_val_score(LogisticRegression(), hiddens, y,cv=2)
print("Logisitic regression average accuracy : ",log.mean())

In [ ]:
nb = cross_val_score(GaussianNB(), hiddens, y,cv=2)
print("Naive bayes average accuracy : ",nb.mean())

In [ ]:
from sklearn.ensemble import RandomForestClassifier
log = cross_val_score(RandomForestClassifier(), hiddens, y,cv=2)
print("Random forest average accuracy : ",log.mean())

In [ ]:
clf = RandomForestClassifier()
clf.fit(hiddens, y)

In [ ]:
from sklearn.ensemble import ExtraTreesClassifier
log = cross_val_score(ExtraTreesClassifier(), hiddens, y,cv=2)
print("Extra trees average accuracy : ",log.mean())

In [ ]:
logreg = LogisticRegression()
logreg.fit(hiddens, y)

## Visualize other hidden state via Logistic

In [ ]:
def evaluate(data):
    hiddenCounter=0
    model.train()
    batch_size = 1
    hidden_init = model.init_hidden(1)
    loss_avg = 0
    for s in range(1):
        model.zero_grad()
        embed_optimizer.zero_grad()
        hidden = hidden_init
        loss =0
        tweet=data
        chars=list(tweet)
        emb = tokenize(tweet)
        embLen=len(emb)
        for i in range(embLen): 
            character1=Variable((torch.Tensor([emb[i]])).long())
            letter=character1.data.numpy()
            character1=embed(character1)
            character1=character1.view(1,1,50)
            output, hidden = model(character1, var(hidden.data))
            
            temp=hidden.view(256)
            temp = temp.data.numpy()
            temp = temp.reshape(1,-1)
            scales=logreg.predict_proba(temp)
            label=logreg.predict(temp)
            if label==0: #control - green 
                text="\033[0;30;42m "+chars[i]
                print (text, end=" ")
            if label==1: #depressed - red
                text="\033[1;30;41m "+chars[i]
                print (text, end=" ")
            if label==2: #ptsd-blue
                text="\033[1;30;44m "+chars[i]
                print (text, end=" ")
            
            output=output.view(1,256)

            if i+1 < embLen: 
                character2=Variable((torch.Tensor([emb[i+1]])).long())
                loss += criterion(output, character2)

        hidden_init = copy_state(hidden)
        loss_avg = .99*loss_avg + .01*loss.data[0]/embLen
        
evaluate('The grass is so nice today')

In [ ]:
#http://ozzmaker.com/add-colour-to-text-in-python/

In [ ]:
import torch
import torch.nn as nn
from torch.autograd import Variable

output = Variable(torch.rand(1,10))
target = Variable(torch.LongTensor([1]))

criterion = nn.CrossEntropyLoss()
loss = criterion(output, target)
print (output)
print(loss)


In [ ]:
confusion_matrix(y_test, y_pred)

In [ ]:
xcm=confusion_matrix(y_test, y_pred, labels=None, sample_weight=None)
xcm=numpy.array(xcm)
ax = sns.heatmap(xcm)
plt.xlabel('Test Labels')
plt.ylabel('Predicted Labels')
#plt.show()
plt.savefig('ConfusionMatrix')